# Complex Imitation Learning in MineRL
This tutorial contains a simple example of how to build a imitation-learning based agent that can solve the MineRLNavigateDense-v0 environment. For more information about that environment, see this [MineRL Docs](http://minerl.io/docs/environments/index.html#minerlnavigatedense-v0).

For more Imitation Learning algorithms, like a Dagger in Tensorflow, see that Github repo, [Dagger](https://github.com/zsdonghao/Imitation-Learning-Dagger-Torcs).

Parts of this tutorial are based on code by [Arthur Juliani](https://medium.com/@awjuliani/super-simple-reinforcement-learning-tutorial-part-2-ded33892c724).

In [1]:
from __future__ import division

import numpy as np
import tensorflow as tf
import tensorflow.contrib.slim as slim
%matplotlib inline
import matplotlib.pyplot as plt
import math

try:
    xrange = xrange
except:
    xrange = range
    
#env_name = 'MineRLTreechop-v0'
env_name = 'MineRLObtainIronPickaxe-v0'
data_path = '/media/kimbring2/6224AA7924AA5039/minerl_data'

/home/kimbring2/minerl_env/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/kimbring2/minerl_env/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/kimbring2/minerl_env/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/kimbring2/minerl_env/lib/python3.6/site-packages/tensorflow/pyth

### Setting up our Neural Network agent
This time we will be using a Policy neural network that takes observations, passes them through a single hidden layer, and then produces a probability of choosing a left/right movement. To learn more about this network, see [Andrej Karpathy's blog on Policy Gradient networks](http://karpathy.github.io/2016/05/31/rl/).

In [6]:
H_1 = 1024
H_2 = 1024

tf.reset_default_graph()

state_pov_1 = tf.placeholder(shape=[None,64,64,3], dtype=tf.float32)
state_item_1 = tf.placeholder(shape=[None,64,64,18], dtype=tf.float32)
conv1_pov_1 = slim.conv2d(inputs=state_pov_1, num_outputs=3, kernel_size=[2,2], stride=[1,1], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv2_pov_1 = slim.conv2d(inputs=conv1_pov_1, num_outputs=3, kernel_size=[2,2], stride=[1,1], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv3_pov_1 = slim.conv2d(inputs=conv2_pov_1, num_outputs=3, kernel_size=[2,2], stride=[1,1], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv1_item_1 = slim.conv2d(inputs=state_item_1, num_outputs=32, kernel_size=[8,8], stride=[4,4], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv2_item_1 = slim.conv2d(inputs=conv1_item_1, num_outputs=64, kernel_size=[4,4], stride=[2,2], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv3_item_1 = slim.conv2d(inputs=conv2_item_1, num_outputs=64, kernel_size=[3,3], stride=[1,1], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
convFlat_pov_1 = slim.flatten(conv3_pov_1)
FC_pov_1 = slim.fully_connected(convFlat_pov_1, 512, scope='fc_pov_1')

convFlat_item_1 = slim.flatten(conv3_item_1)
FC_item_1 = slim.fully_connected(convFlat_item_1, 512, scope='fc_item_1')

print("FC_pov_1: " + str(FC_pov_1))
print("FC_item_1: " + str(FC_item_1))

convFlat_1 = tf.concat([FC_pov_1, FC_item_1], 1)
print("convFlat_1: " + str(convFlat_1))

state_pov_2 = tf.placeholder(shape=[None,64,64,3], dtype=tf.float32)
state_item_2 = tf.placeholder(shape=[None,64,64,18], dtype=tf.float32)
conv1_pov_2 = slim.conv2d(inputs=state_pov_2, num_outputs=3, kernel_size=[2,2], stride=[1,1], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv2_pov_2 = slim.conv2d(inputs=conv1_pov_2, num_outputs=3, kernel_size=[2,2], stride=[1,1], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv3_pov_2 = slim.conv2d(inputs=conv2_pov_2, num_outputs=3, kernel_size=[2,2], stride=[1,1], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv1_item_2 = slim.conv2d(inputs=state_item_2, num_outputs=32, kernel_size=[8,8], stride=[4,4], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv2_item_2 = slim.conv2d(inputs=conv1_item_2, num_outputs=64, kernel_size=[4,4], stride=[2,2], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
conv3_item_2 = slim.conv2d(inputs=conv2_item_2, num_outputs=64, kernel_size=[3,3], stride=[1,1], padding='VALID', 
                    biases_initializer=None, activation_fn=tf.nn.relu)
convFlat_pov_2 = slim.flatten(conv3_pov_2)
FC_pov_2 = slim.fully_connected(convFlat_pov_2, 512)

convFlat_item_2 = slim.flatten(conv3_item_2)
FC_item_2 = slim.fully_connected(convFlat_item_2, 512)

convFlat_2 = tf.concat([FC_pov_2, FC_item_2], 1)

W_1 = tf.get_variable("W_1", shape=[H_1,21],
            initializer=tf.contrib.layers.xavier_initializer())
score_1 = tf.matmul(convFlat_1, W_1)
probability_1 = tf.nn.softmax(score_1)
real_action_1 = tf.placeholder(shape=[None,21], dtype=tf.int32)
loss_1 = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=real_action_1, 
                                                                logits=score_1))
tf.summary.scalar('loss_1', loss_1)

W_2 = tf.get_variable("W_2", shape=[H_2,20],
            initializer=tf.contrib.layers.xavier_initializer())
score_2 = tf.matmul(convFlat_2, W_2)
probability_2 = tf.nn.softmax(score_2)
real_action_2 = tf.placeholder(shape=[None,20], dtype=tf.int32)
loss_2 = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=real_action_2, 
                                                                logits=score_2))
tf.summary.scalar('loss_2', loss_2)

train_step_1 = tf.train.AdamOptimizer(0.00005).minimize(loss_1)
train_step_2 = tf.train.AdamOptimizer(0.00005).minimize(loss_2)

merged = tf.summary.merge_all()

FC_pov_1: Tensor("fc_pov_1/Relu:0", shape=(?, 512), dtype=float32)
FC_item_1: Tensor("fc_item_1/Relu:0", shape=(?, 512), dtype=float32)
convFlat_1: Tensor("concat:0", shape=(?, 1024), dtype=float32)
Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.



In [13]:
import gym
import minerl

######################################

# Sample some data from the dataset!
env_name = 'MineRLObtainIronPickaxe-v0'
data_path = '/media/kimbring2/6224AA7924AA5039/minerl_data'
data = minerl.data.make(env_name, data_path)

# Iterate through a single epoch using sequences of at most 32 steps
for current_state, action, reward, next_state, done in data.sarsd_iter(num_epochs=500, max_sequence_len=20):
    # Do something
    #print("current_state['inventory']: " + str(current_state['inventory']))
    print("action['camera']: " + str(action['camera']))
    print("action['jump']: " + str(action['jump']))

action['camera']: [[  1.6499977   -2.850006  ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.14999962  -1.3500061 ]
 [ -0.          -3.75      ]
 [ -0.          -3.1500092 ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.74999905  -1.3499985 ]
 [  1.0499983   -1.5000076 ]
 [  0.14999962  -0.15000153]
 [  0.14999962  -0.15000153]
 [ -0.          -0.30000305]
 [  0.           0.        ]
 [  0.           0.        ]
 [ -0.          -0.15000153]
 [  0.14999962  -2.7000046 ]
 [  0.3000002  -11.099991  ]
 [ -0.          -7.7999954 ]
 [  0.           0.        ]]
action['jump']: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
action['camera']: [[-0.          0.15000153]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [-0.44999886  1.6500092 ]
 [-0.4499998   1.3500137 ]
 [-0.          0.45000458]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 

action['jump']: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
action['camera']: [[ 0.          0.        ]
 [ 0.          0.        ]
 [-0.          1.5       ]
 [-0.          2.399994  ]
 [-0.          0.30000305]
 [-0.          0.6000061 ]
 [-0.          0.45000458]
 [-0.          0.15000153]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [-0.          0.6000061 ]
 [-0.          0.7500076 ]
 [ 0.          0.        ]
 [ 0.          0.        ]]
action['jump']: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
action['camera']: [[ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [-1.050003    0.30000305]
 [-2.5499954   0.6000061 ]
 [-0.6000061   0.15000153]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.15000153  0.15000153]
 [ 0.30000305  0.30000305]
 [ 0.     

action['jump']: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
action['camera']: [[0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]]
action['jump']: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
action['camera']: [[0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]]
action['jump']: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
action['camera']: [[0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]]
action['jump']: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
action['camera']: [[0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]


action['camera']: [[ -0.          -1.199997  ]
 [ -0.          -3.7499847 ]
 [ -0.         -17.849998  ]
 [ -0.         -20.399986  ]
 [ -0.          -9.899994  ]
 [  0.           0.        ]
 [ -0.29999995  -0.        ]
 [ -0.           0.15000153]
 [ -0.44999993   0.30000305]
 [  0.           0.        ]
 [ -0.45000002   0.7500076 ]
 [ -0.           0.15000153]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [ -0.15        -0.45000458]
 [ -0.          -0.90000916]
 [  0.           0.        ]
 [ -0.          -0.30000305]]
action['jump']: [1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1]
action['camera']: [[ 1.4901161e-08  1.5000153e-01]
 [-0.0000000e+00 -1.5000153e-01]
 [ 0.0000000e+00  0.0000000e+00]
 [-1.5000001e-01 -0.0000000e+00]
 [-6.0000002e-01  7.5000763e-01]
 [-1.2000000e+00 -2.5499954e+00]
 [ 1.4999998e-01 -1.6500015e+00]
 [ 2.9999995e-01 -1.6499786e+00]
 [-0.0000000e+00 -1.4999390e-01]
 [ 1.4999998e-01 -1.9499969e

action['camera']: [[-0.         -2.2499695 ]
 [-0.         -0.1499939 ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [-0.         -0.5999756 ]
 [ 0.15000004 -1.0499573 ]
 [-0.14999998 -1.7999573 ]
 [ 0.          0.        ]
 [-0.         -1.0499573 ]
 [-0.14999998 -0.5999756 ]]
action['jump']: [0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1]
action['camera']: [[  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           0.        ]
 [  0.           

...

action['camera']: [[ -2.3999996   -0.1499939 ]
 [ -0.29999924  -1.050003  ]
 [  0.14999962  -1.5       ]
 [  0.14999962  -1.6500092 ]
 [  0.14999962  -2.25      ]
 [ -0.          -7.949997  ]
 [ -0.         -14.550003  ]
 [ -0.3000002  -10.800018  ]
 [ -0.3000002   -3.4500122 ]
 [ -0.          -0.1499939 ]
 [ -3.5999994    3.75      ]
 [ -7.2         15.300018  ]
 [ -6.3         13.199997  ]
 [ -1.8000002    7.949997  ]
 [ -0.           4.800003  ]
 [ -0.           6.449997  ]
 [ -0.           8.099991  ]
 [ -0.           3.449997  ]
 [  0.29999924  -0.1499939 ]
 [  0.           0.        ]]
action['jump']: [0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0]
action['camera']: [[0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]]
action['jump']: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
action['camera']: [[ -0.15000153  -1.3500366 ]
 [ -0.30000305  -0.5999756 ]
 [ -0.    

action['camera']: [[-0.06672668 -0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [-0.06672668 -0.        ]
 [-0.         -0.06672668]
 [-0.06672668 -0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]]
action['jump']: [0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
action['camera']: [[-0.29999924  0.2999878 ]
 [-0.29999924  1.0499878 ]
 [ 0.6000004   2.699997  ]
 [ 4.200001    4.950012  ]
 [ 4.3500023   2.399994  ]
 [ 3.1500015  -0.30000305]
 [ 0.6000023  -0.1499939 ]
 [ 0.          0.        ]
 [-0.         -0.1499939 ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.          0.        ]
 [ 0.         

Process ForkPoolWorker-233:
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/pool.py", line 119, in worker
    result = (True, func(*args, **kwds))


KeyboardInterrupt: 

  File "/usr/lib/python3.6/multiprocessing/pool.py", line 47, in starmapstar
    return list(itertools.starmap(args[0], args[1]))
  File "/home/kimbring2/minerl_env/lib/python3.6/site-packages/minerl/data/data_pipeline.py", line 323, in _load_data_pyfunc
    ret, frame = cap.read()
Process ForkPoolWorker-236:
Process ForkPoolWorker-234:
KeyboardInterrupt
Process ForkPoolWorker-235:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/pool.py", line 47, in starmapstar
    return list(itertools.starmap(args[0], args[1]))
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/pool.py", line 119, in worker
    result = (True, func(*args, **kwds))
  File "/usr/lib/python3.6/multiprocessing/process.py

# Train
MineRL package provides a human playing dataset for improving effiency of traning. At first, we are going to train our network by this dataset and use pretrained network for Reinforcement Learning. I assure it will reduce traing time tremendously. 

For more information about that dataset, see this [MineRL Dataset Docs](http://minerl.io/docs/tutorials/data_sampling.html).

### Running the Agent and Environment

In [7]:
import minerl
data = minerl.data.make(env_name, data_path)

init = tf.global_variables_initializer()
restore = False
with tf.Session() as sess:
    rendering = False
    sess.run(init)
    saver = tf.train.Saver(max_to_keep=5)
    train_writer = tf.summary.FileWriter('/home/kimbring2/MineRL/train_summary/' + env_name, sess.graph)
    
    if restore == True:
        path = '/home/kimbring2/MineRL/model/' + env_name
        ckpt = tf.train.get_checkpoint_state(path)
        saver.restore(sess, ckpt.model_checkpoint_path)
    
    episode_count = 0
    for current_state, action, reward, next_state, done in data.sarsd_iter(num_epochs=500, max_sequence_len=200):
        #print("action: " + str(action))
        #print("current_state['equipped_items']: " + str(current_state['equipped_items']))
        length = (current_state['pov'].shape)[0]

        action1_list = []
        action2_list = []
        states_pov_list = []
        states_item_list =[]
        for i in range(0, length):
            #print("current_state: " + str(current_state))
                
            pov = current_state['pov'][i].astype(np.float32) / 255.0 - 0.5
            
            inventory = current_state['inventory']
            coal = inventory['coal'][i]
            cobblestone = inventory['cobblestone'][i]
            crafting_table = inventory['crafting_table'][i]
            dirt = inventory['dirt'][i]
            furnace = inventory['furnace'][i]
            iron_axe = inventory['iron_axe'][i]
            iron_ingot = inventory['iron_ingot'][i]
            iron_ore = inventory['iron_ore'][i]
            iron_pickaxe = inventory['iron_pickaxe'][i]
            log = inventory['log'][i]
            planks = inventory['planks'][i]
            stick = inventory['stick'][i]
            stone = inventory['stone'][i]
            stone_axe = inventory['stone_axe'][i]
            stone_pickaxe = inventory['stone_pickaxe'][i]
            torch = inventory['torch'][i]
            wooden_axe = inventory['wooden_axe'][i]
            wooden_pickaxe = inventory['wooden_pickaxe'][i]
            '''
            #print("np.ones(shape=list(pov.shape[:-1]): " + str(np.ones(shape=list(pov.shape[:-1]))))
            coal_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * coal
            cobblestone_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * cobblestone
            crafting_table_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * crafting_table
            dirt_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * dirt
            furnace_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * furnace
            iron_axe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * iron_axe
            iron_ingot_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * iron_ingot
            iron_ore_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * iron_ore
            iron_pickaxe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * iron_pickaxe
            log_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * log
            planks_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * planks
            stick_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * stick
            stone_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * stone
            stone_axe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * stone_axe
            stone_pickaxe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * stone_pickaxe
            torch_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * torch
            wooden_axe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * wooden_axe
            wooden_pickaxe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * wooden_pickaxe
            #print("compass_channel: " + str(compass_channel))
            
            state_pov = pov
            state_item = np.concatenate([coal_channel, cobblestone_channel, crafting_table_channel, 
                                         dirt_channel, furnace_channel, iron_axe_channel, iron_ingot_channel,
                                         iron_ore_channel, iron_pickaxe_channel, log_channel, planks_channel, 
                                         stick_channel, stone_channel, stone_axe_channel, stone_pickaxe_channel,
                                         torch_channel, wooden_axe_channel, wooden_pickaxe_channel], axis=-1)
            '''
            #print("state_concat.shape: " + str(state_concat.shape))
            '''
                OrderedDict([('attack', array([0])), ('back', array([0])), ('camera', array([[0., 0.]], dtype=float32)), 
                ('forward', array([0])), ('jump', array([0])), ('left', array([0])), ('place', array([0])), ('right', array([0])),
                ('sneak', array([0])), ('sprint', array([0]))])
            '''
            '''
                camera : 4
                forward / back : 3
                right / left : 3
                sneak / sprint : 3
                attack / place / equip / craft / nearbyCraft / nearbySmelt : 7
                jump : 2
            '''
            
            if (action['attack'][i] == 1):
                action_ = [1, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]                  
            elif (action['place'][i] == 'dirt'):
                action_ = [0, 1, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]             
            elif (action['place'][i] == 'stone'):
                action_ = [0, 0, 1, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]   
            elif (action['place'][i] == 'cobblestone'):
                action_ = [0, 0, 0, 1, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]            
            elif (action['place'][i] == 'crafting_table'):
                action_ = [0, 0, 0, 0, 1, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]             
            elif (action['place'][i] == 'furnace'):
                action_ = [0, 0, 0, 0, 0, 1, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]             
            elif (action['place'][i] == 'torch'):
                action_ = [0, 0, 0, 0, 0, 0, 1, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]         
            elif (action['craft'][i] == 'torch'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 1, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]             
            elif (action['craft'][i] == 'stick'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 1, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]             
            elif (action['craft'][i] == 'planks'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 1,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]             
            elif (action['craft'][i] == 'crafting_table'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           1, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]
            elif (action['nearbyCraft'][i] == 'wooden_axe'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 1, 0, 0, 0, 0, 0, 0, 0, 0,
                           0]             
            elif (action['nearbyCraft'][i] == 'wooden_pickaxe'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 1, 0, 0, 0, 0, 0, 0, 0,
                           0]             
            elif (action['nearbyCraft'][i] == 'stone_axe'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 1, 0, 0, 0, 0, 0, 0,
                           0]             
            elif (action['nearbyCraft'][i] == 'stone_pickaxe'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 1, 0, 0, 0, 0, 0,
                           0]             
            elif (action['nearbyCraft'][i] == 'iron_axe'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 1, 0, 0, 0, 0,
                           0]             
            elif (action['nearbyCraft'][i] == 'iron_pickaxe'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 1, 0, 0, 0,
                           0]
            elif (action['nearbyCraft'][i] == 'furnace'):   
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 1, 0, 0,
                           0]
            elif (action['nearbySmelt'][i] == 'iron_ingot'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 1, 0,
                           0]             
            elif (action['nearbySmelt'][i] == 'coal'):
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 1,
                           0] 
            else: 
                action_ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                           1] 
                             
            #print("abs(action['camera'][i]): " + str(abs(action['camera'][i])))
            #print("abs(action['camera'][i][1]) > abs(action['camera'][i][0])): " + str((abs(action['camera'][i][1]) > abs(action['camera'][i][0]))))
            if ( (action['camera'][i][1] < 0) & (abs(action['camera'][i][0]) > abs(action['camera'][i][0])) ):
                if ( (action['jump'][i] == 0) & (action['forward'][i] == 0) ):
                    action__ = [1, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 0) & (action['forward'][i] == 1) ):
                    action__ = [0, 1, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 0) ):
                    action__ = [0, 0, 1, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 1) ):
                    action__ = [0, 0, 0, 1, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
            elif ( (action['camera'][i][1] < 0) & (action['camera'][i][0] > 0) ):
                if ( (action['jump'][i] == 0) & (action['forward'][i] == 0) ):
                    action__ = [0, 0, 0, 0, 1, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 0) & (action['forward'][i] == 1) ):
                    action__ = [0, 0, 0, 0, 0, 1, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 0) ):
                    action__ = [0, 0, 0, 0, 0, 0, 1, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 1) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 1, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
            elif ( (action['camera'][i][1] > 0) & (action['camera'][i][0] < 0) ):
                if ( (action['jump'][i] == 0) & (action['forward'][i] == 0) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 1, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 0) & (action['forward'][i] == 1) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 1,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 0) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 1) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 1, 0, 0, 0, 0, 0, 0, 0, 0]
            elif ( (action['camera'][i][1] > 0) & (action['camera'][i][0] > 0) ):
                if ( (action['jump'][i] == 0) & (action['forward'][i] == 0) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 1, 0, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 0) & (action['forward'][i] == 1) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 1, 0, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 0) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 1, 0, 0, 0, 0, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 1) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 1, 0, 0, 0, 0]
            else:
                if ( (action['jump'][i] == 0) & (action['forward'][i] == 0) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 1, 0, 0, 0]
                elif ( (action['jump'][i] == 0) & (action['forward'][i] == 1) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 1, 0, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 0) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 1, 0]
                elif ( (action['jump'][i] == 1) & (action['forward'][i] == 1) ):
                    action__ = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
                                0, 0, 0, 0, 0, 0, 0, 0, 0, 1]
            
            #print("action__: " + str(action__))
            states_pov_list.append(state_pov)                                                            
            states_item_list.append(state_item)
            action1_list.append(action_)
            action2_list.append(action__)                                       
        
        episode_count = episode_count + 1
        
        #state_train = (np.zeros([1,H]), np.zeros([1,H]))
        feed_dict = {state_pov_1:np.stack(states_pov_list, 0),
                     state_item_1:np.stack(states_item_list, 0),
                     state_pov_2:np.stack(states_pov_list, 0),
                     state_item_2:np.stack(states_item_list, 0),
                     real_action_1:np.stack(action1_list, 0),
                     real_action_2:np.stack(action2_list, 0)
                    }
        
        if episode_count % 100 == 0:
            summary, _, _ = sess.run([merged, train_step_1, train_step_2], feed_dict=feed_dict)                                   
            train_writer.add_summary(summary, episode_count)

        sess.run(train_step_1, feed_dict=feed_dict)
        sess.run(train_step_2, feed_dict=feed_dict)                                           
        
        if episode_count % 100 == 0:
            model_path = '/home/kimbring2/MineRL/model/' + env_name
            saver.save(sess, model_path + '/model-' + str(episode_count) + '.cptk')
            print("Saved Model")

Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Instructions for updating:
Use standard file APIs to delete files with this prefix.
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model
Saved Model


Process ForkPoolWorker-2:
Process ForkPoolWorker-4:
Traceback (most recent call last):
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/pool.py", line 119, in worker
    result = (True, func(*args, **kwds))
  File "/usr/lib/python3.6/multiprocessing/pool.py", line 47, in starmapstar
    return list(itertools.starmap(args[0], args[1]))
  File "/home/kimbring2/minerl_env/lib/python3.6/site-packages/minerl/data/data_pipeline.py", line 416, in _load_data_pyfunc
    data_queue.put(batches)
  File "<string>", line 2, in put
  File "/usr/lib/python3.6/multiprocessing/managers.py", line 757, in _callmethod
    kind, result = conn.recv()
Process ForkPoolWorker-1:


KeyboardInterrupt: 

Here we run the neural network agent, and have it act in the CartPole environment.

In [ ]:
'''
import minerl
import gym
env = gym.make('MineRLNavigateDense-v0')

obs  = env.reset()
done = False
net_reward = 0

while not done:
    action = env.action_space.noop()

    action['camera'] = [0, -10]
    action['back'] = 0
    action['forward'] = 1
    action['jump'] = 1
    action['attack'] = 1

    obs, reward, done, info = env.step(
        action)

    net_reward += reward
    print("Total reward: ", net_reward)
'''

In [ ]:
#import minerl
#data = minerl.data.make('MineRLNavigateDense-v0', '/home/kimbring2/MineRL/data/')

# Test

In [6]:
import minerl
import gym

env = gym.make('MineRLObtainIronPickaxe-v0')
#obs = env.reset()

In [9]:
import random

e = 0.05

init = tf.global_variables_initializer()
with tf.Session() as sess:
    sess.run(init)
    saver = tf.train.Saver(max_to_keep=5)
    #train_writer = tf.summary.FileWriter('/home/kimbring2/MineRL/train_summary', sess.graph)
    
    print('Loading Model...')
    path = '/home/kimbring2/MineRL/model/' + env_name
    ckpt = tf.train.get_checkpoint_state(path)
    saver.restore(sess, ckpt.model_checkpoint_path)
    
    env.init()
    obs = env.reset()
    net_reward = 0
    while True:
        #print("current_state['inventory']: " + str(current_state['inventory']))
        pov = obs['pov'].astype(np.float32) / 255.0 - 0.5
        inventory = obs['inventory']
        #print("compass: " + str(compass))
                
        coal = inventory['coal']
        cobblestone = inventory['cobblestone']
        crafting_table = inventory['crafting_table']
        dirt = inventory['dirt']
        furnace = inventory['furnace']
        iron_axe = inventory['iron_axe']
        iron_ingot = inventory['iron_ingot']
        iron_ore = inventory['iron_ore']
        iron_pickaxe = inventory['iron_pickaxe']
        log = inventory['log']
        planks = inventory['planks']
        stick = inventory['stick']
        stone = inventory['stone']
        stone_axe = inventory['stone_axe']
        stone_pickaxe = inventory['stone_pickaxe']
        torch = inventory['torch']
        wooden_axe = inventory['wooden_axe']
        wooden_pickaxe = inventory['wooden_pickaxe']
                
        #print("np.ones(shape=list(pov.shape[:-1]): " + str(np.ones(shape=list(pov.shape[:-1]))))
        coal_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * coal
        cobblestone_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * cobblestone
        crafting_table_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * coal
        dirt_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * dirt
        furnace_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * furnace
        iron_axe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * iron_axe
        iron_ingot_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * iron_ingot
        iron_ore_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * iron_ore
        iron_pickaxe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * iron_pickaxe
        log_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * log
        planks_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * planks
        stick_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * stick
        stone_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * stone
        stone_axe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * stone_axe
        stone_pickaxe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * stone_pickaxe
        torch_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * torch
        wooden_axe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * wooden_axe
        wooden_pickaxe_channel = np.ones(shape=list(pov.shape[:-1]) + [1], dtype=np.float32) * wooden_pickaxe
        #print("compass_channel: " + str(compass_channel))
                
        state_pov = pov
        state_item = np.concatenate([coal_channel, cobblestone_channel, crafting_table_channel, 
                                    dirt_channel, furnace_channel, iron_axe_channel, iron_ingot_channel,
                                    iron_ore_channel, iron_pickaxe_channel, log_channel, planks_channel, 
                                    stick_channel, stone_channel, stone_axe_channel, stone_pickaxe_channel,
                                    torch_channel, wooden_axe_channel, wooden_pickaxe_channel], axis=-1)
            
        action = env.action_space.noop()
        action1_probability = sess.run(probability_1, feed_dict={state_pov_1:[state_pov],
                                                                 state_item_1:[state_item],
                                                                 state_pov_2:[state_pov],
                                                                 state_item_2:[state_item]})
        if np.random.rand(1) >= e:
            action1_index = np.argmax(action1_probability)
        else:  
            action1_index = random.randint(0,21)
        
        if (action1_index == 0):
            action['attack'] = 1; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
                
        elif (action1_index == 1):
            action['attack'] = 0; action['place'] = 'dirt'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
        elif (action1_index == 2):
            action['attack'] = 0; action['place'] = 'stone'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
        elif (action1_index == 3):
            action['attack'] = 0; action['place'] = 'cobblestone'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
        elif (action1_index == 4):
            action['attack'] = 0; action['place'] = 'crafting_table'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
        elif (action1_index == 5):
            action['attack'] = 0; action['place'] = 'furnace'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
        elif (action1_index == 6):
            action['attack'] = 0; action['place'] = 'torch'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
                
        elif (action1_index == 7):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'torch'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
        elif (action1_index == 8):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'stick'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
        elif (action1_index == 9):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'planks'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
        elif (action1_index == 10):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'crafting_table'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
                
        elif (action1_index == 11):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'wooden_axe'; action['nearbySmelt'] = 'none'
        elif (action1_index == 12):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'wooden_pickaxe'; action['nearbySmelt'] = 'none'
        elif (action1_index == 13):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'stone_axe'; action['nearbySmelt'] = 'none'
        elif (action1_index == 14):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'stone_pickaxe'; action['nearbySmelt'] = 'none'
        elif (action1_index == 15):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'iron_axe'; action['nearbySmelt'] = 'none'
        elif (action1_index == 16):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'iron_pickaxe'; action['nearbySmelt'] = 'none'
        elif (action1_index == 17):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'furnace'; action['nearbySmelt'] = 'none'
                
        elif (action1_index == 18):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'iron_ingot'
        elif (action1_index == 19):
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'coal'
        else:
            action['attack'] = 0; action['place'] = 'none'; action['craft'] = 'none'; 
            action['nearbyCraft'] = 'none'; action['nearbySmelt'] = 'none'
                

        action2_probability = sess.run(probability_2, feed_dict={state_pov_1:[state_pov],
                                                                 state_item_1:[state_item],
                                                                 state_pov_2:[state_pov],
                                                                 state_item_2:[state_item]})
        if np.random.rand(1) >= e:
            action2_index = np.argmax(action2_probability)   
        else:    
            action2_index = random.randint(0,20)
        
        if (action2_index == 0):
            action['camera'][0] = -10; action['camera'][1] = -10; action['forward'] = 0; action['jump'] = 0; 
        elif (action2_index == 1):
            action['camera'][0] = -10; action['camera'][1] = -10; action['forward'] = 0; action['jump'] = 1; 
        elif (action2_index == 2):
            action['camera'][0] = -10; action['camera'][1] = -10; action['forward'] = 1; action['jump'] = 0; 
        elif (action2_index == 3):
            action['camera'][0] = -10; action['camera'][1] = -10; action['forward'] = 1; action['jump'] = 1; 
                
        elif (action2_index == 4):
            action['camera'][0] = -10; action['camera'][1] = 10; action['forward'] = 0; action['jump'] = 0; 
        elif (action2_index == 5):
            action['camera'][0] = -10; action['camera'][1] = 10; action['forward'] = 0; action['jump'] = 1; 
        elif (action2_index == 6):
            action['camera'][0] = -10; action['camera'][1] = 10; action['forward'] = 1; action['jump'] = 0; 
        elif (action2_index == 7):
            action['camera'][0] = -10; action['camera'][1] = 10; action['forward'] = 1; action['jump'] = 1;  
                
        elif (action2_index == 8):
            action['camera'][0] = 10; action['camera'][1] = -10; action['forward'] = 0; action['jump'] = 0; 
        elif (action2_index == 9):
            action['camera'][0] = 10; action['camera'][1] = -10; action['forward'] = 0; action['jump'] = 1; 
        elif (action2_index == 10):
            action['camera'][0] = 10; action['camera'][1] = -10; action['forward'] = 1; action['jump'] = 0; 
        elif (action2_index == 11):
            action['camera'][0] = 10; action['camera'][1] = -10; action['forward'] = 1; action['jump'] = 1;              
                
        elif (action2_index == 12):
            action['camera'][0] = 10; action['camera'][1] = 10; action['forward'] = 0; action['jump'] = 0; 
        elif (action2_index == 13):
            action['camera'][0] = 10; action['camera'][1] = 10; action['forward'] = 0; action['jump'] = 1; 
        elif (action2_index == 14):
            action['camera'][0] = 10; action['camera'][1] = 10; action['forward'] = 1; action['jump'] = 0; 
        elif (action2_index == 15):
            action['camera'][0] = 10; action['camera'][1] = 10; action['forward'] = 1; action['jump'] = 1;  
                
        elif (action2_index == 16):
            action['camera'][0] = 0; action['camera'][1] = 0; action['forward'] = 0; action['jump'] = 0; 
        elif (action2_index == 17):
            action['camera'][0] = 0; action['camera'][1] = 0; action['forward'] = 0; action['jump'] = 1; 
        elif (action2_index == 18):
            action['camera'][0] = 0; action['camera'][1] = 0; action['forward'] = 1; action['jump'] = 0; 
        elif (action2_index == 19):
            action['camera'][0] = 0; action['camera'][1] = 0; action['forward'] = 1; action['jump'] = 1;                  
                
        #print("action: " + str(action))
        #print("action['attack']: " + str(action['attack']))
        action['back'] = 0
        action['left'] = 0
        action['right'] = 0
        action['sprint'] = 0

        obs1, reward, done, info = env.step(action)
        
        if done == True:
            break

    net_reward += reward
    print("Total reward: ", net_reward)

Loading Model...
INFO:tensorflow:Restoring parameters from /home/kimbring2/MineRL/model/MineRLObtainIronPickaxe-v0/model-14200.cptk
Total reward:  0.0


As you can see, the network not only does much better than random actions, but achieves the goal of 200 points per episode, thus solving the task!